This review contains some representative problems to prepare for the first midterm exam.

# 1. nearby rational approximations

Consider $S = \sqrt{2}$

1. Construct a nearby rational approximation for $S$ where the size of the denominator is not larger than 1000.

2. Construct a sequence of 10 nearby rational approximations, where the denominator of the $k$-th approximation is smaller than $10^k$.

3. Verify the accuracy of the rational approximations.

In [1]:
S = sqrt(2)

In [2]:
q = RR(S).nearby_rational(max_denominator=1000)
q

1393/985

In [3]:
R100 = RealField(prec=100)

In [4]:
Q = [R100(S).nearby_rational(max_denominator=10^k) for k in range(1,11)]
Q

[7/5,
 140/99,
 1393/985,
 8119/5741,
 114243/80782,
 941664/665857,
 9369319/6625109,
 131836323/93222358,
 1086679440/768398401,
 10812186007/7645370045]

In [5]:
[floor(abs(log(abs(S - q)/abs(S), 10.0))) for q in Q]

[1, 4, 6, 8, 10, 11, 14, 16, 18, 20]

Observe the increase in precision from ``RR`` (default 53 bits) to 100 bits in ``R100``.

# 2. a function to store data

Define a function ``whatis`` which stores definitions.

Here is a session with this function:

1. ``whatis('computer algebra')`` returns

   ``call again with the definition for computer algebra``
   
   
2. ``whatis('computer algebra', 'the study of algorithms in symbolic computation')`` 

   stores the definition for ``'computer algebra'``
   
   
3. ``whatis('computer algebra')`` returns

   ``the study of algorithms in symbolic computation``

In [6]:
def whatis(name, *definition, D={}):
    if name in D:
        print(name,'is', D[name])
    else:
        if(len(definition) > 0):
            D[name] = definition[0]
        else:
            print('call again with the definition for', name)

In [7]:
whatis('computer algebra')

call again with the definition for computer algebra


In [8]:
whatis('computer algebra', 'the study of algorithms in symbolic computation')

In [9]:
whatis('computer algebra')

computer algebra is the study of algorithms in symbolic computation


In [10]:
whatis('symbolic computation')

call again with the definition for symbolic computation


Using this function could be a good preparation to study the definitions we encountered in the course.

# 3. Algebraic Numbers

Consider the polynomial $p = x^4 + x^2 + 1$
over the field ${\mathbb Z}_2$, the field of bits, 0 and 1.
   
   1. Is $p$ irreducible?  If not, then what are its factors?
   
   2. Extend the field ${\mathbb Z}_2$ with sufficiently many formal roots
      so $p$ factors as a product of linear factors.
      
      Write the factorization of $p$.

In [11]:
reset()
x = polygen(GF(2))
p = x^4 + x^2 + 1
print('Is', p, 'irreducible?', p.is_irreducible())

Is x^4 + x^2 + 1 irreducible? False


The polynomial is not irreducible, it factors.

In [12]:
factor(p)

(x^2 + x + 1)^2

We see that the polynomial is the square of $x^2 + x + 1$.

To define the field extension, we select the irreducible factor from the list of factors.

In [13]:
L = list(factor(p))
L

[(x^2 + x + 1, 2)]

In [14]:
f = L[0][0]
K.<r> = GF(2).extension(f)
K

Finite Field in r of size 2^2

To see the factorization, we must cast the polynomial into the polynomial ring over this extended field.

In [15]:
factor(K[x](p))

(x + r)^2 * (x + r + 1)^2

# 4. Vectorization

Write a Python function ``python_sum`` which takes on input a positive integer $n$ and which returns
the floating-point value of

$$
    \frac{\pi}{n} \sum_{i=1}^{n-1} \cos\left( - \frac{\pi}{2} + i \frac{\pi}{n} \right).
$$

Write a more efficient version ``numpy_sum`` using vectorization.

Time the two versions to illustrate the efficiency.

In [16]:
def python_sum(n):
    """
    Returns the sum of cos(-pi/2 + i*(pi/n)) for i from 1 to n-1.
    """
    return float((pi/n)*sum([cos(-pi/2 + i*(pi/n)) for i in range(1,n)]))

In [17]:
python_sum(1000)

1.9999983550656617

To prepare the ``numpy`` version, let us experiment with ``arange`` for ``n`` equal to 10.

In [18]:
from numpy import arange

In [19]:
arange(10)*(pi/10) - pi/2

array([-1/2*pi, -2/5*pi, -3/10*pi, -1/5*pi, -1/10*pi, 0, 1/10*pi, 1/5*pi,
       3/10*pi, 2/5*pi], dtype=object)

In [20]:
def numpy_sum(n):
    """
    Applies numpy vectors to sum cos(-pi/2 + i*(pi/n)) for i from 1 to n-1.
    """
    from numpy import arange, cos, pi
    x = arange(n-1)*(pi/n) - pi/2
    c = cos(x)
    return (pi/n)*sum(c)

In [21]:
numpy_sum(1000)

1.9999884854774963

In [22]:
timeit('python_sum(1000)')

25 loops, best of 3: 21.2 ms per loop

In [23]:
timeit('numpy_sum(1000)')

625 loops, best of 3: 10.4 μs per loop

We see an enormous speed up, from 72 milliseconds to 31 microseconds.

# 5. Fully Factored Form of Rational Polynomials

Explain what is the fully factored normal form of rational polynomials.

Why does this automatic simplification not happen automatically?

Illustrate with a good example.

### answer:

The fully factored normal form of the rational polynomial is where both numerator and denominator are factored and where the common factor is removed.

In [24]:
reset()
x = var('x')
q = (x^2 - 1)/(x+1)
show(q)

(x^2 - 1)/(x + 1)

In [25]:
print('normalized numerator :', q.numerator(normalize=True))
print('normalized denominator :', q.denominator(normalize=True))

normalized numerator : x - 1
normalized denominator : 1


Because of expression swell, this normalization does not happen automatically.  An example is

$$
   \frac{x^{1000} - 1}{x - 1}
$$

which leads to 1000 terms if the $x-1$ is factored out of the numerator.

# 6. Expression Trees

Type 
``reset(); x, y = var('x,y'); q = (x^2 - y)/(y^2 - x)``
and draw the expression tree of ``q.``

In [26]:
reset()
x, y = var('x, y')
q = (x^2 - y)/(y^2 - x)

Let us ask for the operands and the operators.

In [27]:
L0 = q.operands()
print(q.operator(), 'operates on', L0) 
L1 = [(a.operands(), a.operator()) for a in L0]
L1

<function mul_vararg at 0x7f4f37c9aef0> operates on [x^2 - y, 1/(y^2 - x)]


[([x^2, -y], <function add_vararg at 0x7f4f37c9ae60>),
 ([y^2 - x, -1], <built-in function pow>)]

Observe that the division by ``(y^2 - x)`` is represented by ``(y^2 - x)^(-1)``.

We continue computing the operators and the operands.

In [28]:
L2 = L1[0][0]
L3 = L1[1][0]
L4 = [(a.operands(), a.operator()) for a in L2]
L5 = [(a.operands(), a.operator()) for a in L3]
print(L4)
print(L5)

[([x, 2], <built-in function pow>), ([y, -1], <function mul_vararg at 0x7f4f37c9aef0>)]
[([y^2, -x], <function add_vararg at 0x7f4f37c9ae60>), ([], None)]


There are two expressions, ``y^2`` and ``-x``, which have operands and an operator.

In [29]:
L6 = L5[0][0]
[(a.operands(), a.operator()) for a in L6]

[([y, 2], <built-in function pow>),
 ([x, -1], <function mul_vararg at 0x7f4f37c9aef0>)]

Now we represent ``y^2`` and ``-x`` with ``LabelledOrderedTree`` objects.

The next line is needed only if you are running WSL.

In [30]:
sage.typeset.ascii_art.AsciiArt._terminal_width = lambda x: 80

In [31]:
leafy = LabelledOrderedTree([], label='y')
leaf2 = LabelledOrderedTree([], label='2')
nodey2 = LabelledOrderedTree([leafy, leaf2], label='^')
leafx = LabelledOrderedTree([], label='x')
leafm1 = LabelledOrderedTree([], label='-1')
nodexm1 = LabelledOrderedTree([leafx, leafm1], label='*')
print(ascii_art(nodey2))
print(ascii_art(nodexm1))

  ^_
 / /
y 2
  *_
 / / 
x -1


In the same fashion, we represent ``x^2`` and ``-y``.

In [32]:
nodex2 = LabelledOrderedTree([leafx, leaf2], label='^')
nodeym1 = LabelledOrderedTree([leafy, leafm1], label='*')
print(ascii_art(nodex2))
print(ascii_art(nodeym1))

  ^_
 / /
x 2
  *_
 / / 
y -1


The numerator is ``x^2 - y`` and the denominator ``y^2 - x``.

In [33]:
numerator = LabelledOrderedTree([nodex2, nodeym1], label='+')
denominator = LabelledOrderedTree([nodey2, nodexm1], label='+')
print(ascii_art(numerator))
print(ascii_art(denominator))

    _+___
   /    /  
  ^_   *_
 / /  / / 
x 2  y -1
    _+___
   /    /  
  ^_   *_
 / /  / / 
y 2  x -1


Then at last, we take the inverse of the denominator
and multiply with the numerator.

In [34]:
invden = LabelledOrderedTree([denominator, leafm1], label='^')
exptree = LabelledOrderedTree([numerator, invden], label="*")
ascii_art(exptree)

       _______*________
      /               /     
    _+___          __^____
   /    /         /      / 
  ^_   *_       _+___   -1
 / /  / /      /    /  
x 2  y -1     ^_   *_  
             / /  / /  
            y 2  x -1  

# 7. Manipulation of Expressions

Rewrite

$$
   x + \frac{(x - y)^5}{(x + y)^5}
$$

into

$$
   \frac{(x + y)^5 \cdot x + (x - y)^5}{(x + y)^5}.
$$

In [35]:
reset()
x, y = var('x, y')
p = x + (x-y)^5/(x+y)^5
show(p)

x + (x - y)^5/(x + y)^5

We need to prevent ``x+y`` and ``x-y`` from expanding.  We will replace ``x+y`` and ``x-y`` by two new variables, which we must declare first.

In [36]:
u, v = var('u, v')
q = p.subs({x+y:u, x-y:v})
show(q)

x + v^5/u^5

In [37]:
f = factor(q)
show(f)

(u^5*x + v^5)/u^5

In [38]:
show(f(u=x+y,v=x-y))

((x + y)^5*x + (x - y)^5)/(x + y)^5

# 8. Multivariate Polynomials

Consider $p = -y^2 z^3 - y z^4 + 3 x y^3 + x^3 + z^2$
as a polynomial with integer coefficients in the variables $x$, $y$, and $z$.
   
The monomials of $p$ are sorted in the degree lexicographical order.
   
Convert $p$ (*without retyping $p$!*) into the pure lexicographical term order.

In [39]:
reset()
R.<x,y,z> = PolynomialRing(ZZ)
p = -y^2*z^3 - y*z^4 + 3*x*y^3 + x^3 + z^2
show(p)

-y^2*z^3 - y*z^4 + 3*x*y^3 + x^3 + z^2

In [40]:
Rlex.<x,y,z> = PolynomialRing(ZZ, order='lex')
q = Rlex(p)
show(q)

x^3 + 3*x*y^3 - y^2*z^3 - y*z^4 + z^2